# Library setup

In [0]:
!pip install plotnine
!pip install jsonlines
!pip install requests_toolbelt
!pip install requests
!pip install urllib3
!pip install gql[all]

Requirement already satisfied: plotnine in /databricks/python3/lib/python3.8/site-packages (0.8.0)
Requirement already satisfied: statsmodels>=0.12.1 in /databricks/python3/lib/python3.8/site-packages (from plotnine) (0.12.2)
Requirement already satisfied: matplotlib>=3.1.1 in /databricks/python3/lib/python3.8/site-packages (from plotnine) (3.5.2)
Requirement already satisfied: numpy>=1.19.0 in /databricks/python3/lib/python3.8/site-packages (from plotnine) (1.20.1)
Requirement already satisfied: mizani>=0.7.3 in /databricks/python3/lib/python3.8/site-packages (from plotnine) (0.7.4)
Requirement already satisfied: pandas>=1.1.0 in /databricks/python3/lib/python3.8/site-packages (from plotnine) (1.4.2)
Requirement already satisfied: patsy>=0.5.1 in /databricks/python3/lib/python3.8/site-packages (from plotnine) (0.5.1)
Requirement already satisfied: scipy>=1.5.0 in /databricks/python3/lib/python3.8/site-packages (from plotnine) (1.6.2)
Requirement already satisfied: descartes>=1.1.0 in /databricks/python3/lib/python3.8/site-packages (from plotnine) (1.1.0)
Requirement already satisfied: fonttools>=4.22.0 in /databricks/python3/lib/python3.8/site-packages (from matplotlib>=3.1.1->plotnine) (4.33.3)
Requirement already satisfied: kiwisolver>=1.0.1 in /databricks/python3/lib/python3.8/site-packages (from matplotlib>=3.1.1->plotnine) (1.3.1)
Requirement already satisfied: cycler>=0.10 in /databricks/python3/lib/python3.8/site-packages (from matplotlib>=3.1.1->plotnine) (0.10.0)
Requirement already satisfied: pillow>=6.2.0 in /databricks/python3/lib/python3.8/site-packages (from matplotlib>=3.1.1->plotnine) (8.2.0)
Requirement already satisfied: pyparsing>=2.2.1 in /databricks/python3/lib/python3.8/site-packages (from matplotlib>=3.1.1->plotnine) (2.4.7)
Requirement already satisfied: python-dateutil>=2.7 in /databricks/python3/lib/python3.8/site-packages (from matplotlib>=3.1.1->plotnine) (2.8.1)
Requirement already satisfied: packaging>=20.0 in /databricks/python3/lib/python3.8/site-packages (from matplotlib>=3.1.1->plotnine) (21.3)
Requirement already satisfied: six in /databricks/python3/lib/python3.8/site-packages (from cycler>=0.10->matplotlib>=3.1.1->plotnine) (1.15.0)
Requirement already satisfied: palettable in /databricks/python3/lib/python3.8/site-packages (from mizani>=0.7.3->plotnine) (3.3.0)
Requirement already satisfied: pytz>=2020.1 in /databricks/python3/lib/python3.8/site-packages (from pandas>=1.1.0->plotnine) (2020.5)
 WARNING: You are using pip version 21.0.1; however, version 22.1.1 is available.
You should consider upgrading via the '/databricks/python3/bin/python -m pip install --upgrade pip' command. 
Requirement already satisfied: jsonlines in /databricks/python3/lib/python3.8/site-packages (3.0.0)
Requirement already satisfied: attrs>=19.2.0 in /databricks/python3/lib/python3.8/site-packages (from jsonlines) (20.3.0)
 WARNING: You are using pip version 21.0.1; however, version 22.1.1 is available.
You should consider upgrading via the '/databricks/python3/bin/python -m pip install --upgrade pip' command. 
Requirement already satisfied: requests_toolbelt in /databricks/python3/lib/python3.8/site-packages (0.9.1)
Requirement already satisfied: requests<3.0.0,>=2.0.1 in /databricks/python3/lib/python3.8/site-packages (from requests_toolbelt) (2.27.1)
Requirement already satisfied: certifi>=2017.4.17 in /databricks/python3/lib/python3.8/site-packages (from requests<3.0.0,>=2.0.1->requests_toolbelt) (2020.12.5)
Requirement already satisfied: charset-normalizer~=2.0.0 in /databricks/python3/lib/python3.8/site-packages (from requests<3.0.0,>=2.0.1->requests_toolbelt) (2.0.12)
Requirement already satisfied: urllib3<1.27,>=1.21.1 in /databricks/python3/lib/python3.8/site-packages (from requests<3.0.0,>=2.0.1->requests_toolbelt) (1.26.9)
Requirement already satisfied: idna<4,>=2.5 in /databricks/python3/lib/python3.8/site-packages (from requests<3.0.0,>=2.0.1->requests_toolbelt) (2.10)

In [0]:
from gql import gql, Client
from gql.transport.requests import RequestsHTTPTransport

import pyspark.sql.functions as F
from pyspark.sql.types import (ArrayType, LongType, StringType, StructField, StructType, DoubleType, MapType)

import json
import jsonlines
import pandas as pd
import altair as alt
import os

import matplotlib as plt


# Part 1
Extract all SafeGraph monthly data for one state for two months and load your data into a Databricks database (Team)

In [0]:
url = 'https://api.safegraph.com/v2/graphql'

%run ./keys

In [0]:
#os.mkdir('/tmp/safegraph')
#os.mkdir('/tmp/safegraph/cgjde')
dbutils.fs.mkdirs("/FileStore/Team-CGJDE/safegraph")
#dbutils.fs.rm("/FileStore/Team-CGJDE/safegraph/ut_jun_jul_2021", True)
dbutils.fs.mkdirs("/FileStore/Team-CGJDE/safegraph/ut_jun_jul_2021")

Out[4]: True

# Initiate API connection
transport = RequestsHTTPTransport(
    url=url,
    verify=True,
    retries=3,
    headers={'Content-Type': 'application/json', 'apikey': SAFEGRAPH_KEY})

client = Client(transport=transport, fetch_schema_from_transport=True)

In [0]:
# schema setup
schema = StructType([
  StructField("placekey",StringType(),True),
  StructField("location_name",StringType(),True),
  StructField("parent_placekey",StringType(),True),
  StructField("street_address",StringType(),True),
  StructField("city",StringType(),True),
  StructField("date_range_end",StringType(),True),
  StructField("date_range_start",StringType(),True),
  StructField("poi_cbg",StringType(),True),
  StructField("postal_code", StringType(),True),
  StructField("iso_country_code",StringType(),True), 
  StructField("median_dwell",DoubleType(),True),
  StructField("raw_visit_counts",LongType(),True),
  StructField("raw_visitor_counts",LongType(),True),
  StructField("visits_by_day", ArrayType(LongType(), True)),
  StructField("region",StringType(),True),
  StructField("device_type", MapType(StringType(), LongType(), True)),
  StructField("bucketed_dwell_times", MapType(StringType(), LongType(), True)),
  StructField("distance_from_home",LongType(),True),
  StructField("related_same_day_brand", MapType(StringType(), LongType(), True)),
  StructField("related_same_month_brand", MapType(StringType(), LongType(), True)),
  StructField("visitor_country_of_origin", MapType(StringType(), LongType(), True)),
  StructField("visitor_daytime_cbgs", MapType(StringType(), LongType(), True)),
  StructField("visitor_home_aggregation", MapType(StringType(), LongType(), True)),
  StructField("visitor_home_cbgs", MapType(StringType(), LongType(), True)),
  StructField("normalized_visits_by_total_visits",DoubleType(),True),
  StructField("normalized_visits_by_state_scaling",DoubleType(),True),
  StructField("normalized_visits_by_total_visitors",DoubleType(),True),
  StructField("normalized_visits_by_region_naics_visits",DoubleType(),True),
  StructField("normalized_visits_by_region_naics_visitors",DoubleType(),True)
])

schema_core = StructType([
  StructField("placekey",  StringType(),True),
  StructField("location_name",  StringType(),True),
  StructField('brands', ArrayType(MapType(StringType(), StringType(), True))),
  StructField("naics_code", LongType(),True),
  StructField("latitude", DoubleType(),True),
  StructField("longitude", DoubleType(),True),
  StructField("street_address",  StringType(),True),
  StructField("city",  StringType(),True),
  StructField("postal_code",  StringType(),True),
  StructField("region",  StringType(),True),
  StructField("closed_on",  StringType(),True),
  StructField("opened_on",  StringType(),True),
  StructField("parent_placekey",  StringType(),True)
])

print("Read `schema_rm`, 'schema' and 'schema_core'")

Read `schema_rm`, 'schema' and 'schema_core'

In [0]:
# weekly_patterns function

query_sg = """query {
  search(filter: { 
     --FILTERS--
    address: {
      region: "--STATENAME--"
    }
  }){
    places {
      results(first: 500 after: "--ENDCURSER--") {
        pageInfo { hasNextPage, endCursor}
        edges {
          node {
            monthly_patterns (start_date: "--DATESTART--" end_date: "--DATEEND--") {
              placekey
              parent_placekey
              location_name
              street_address
              city
              region
              postal_code
              iso_country_code
              date_range_start
              date_range_end
              raw_visit_counts
              raw_visitor_counts
              visits_by_day
              device_type
              poi_cbg
              visitor_home_cbgs
              visitor_home_aggregation
              visitor_daytime_cbgs
              visitor_country_of_origin
              distance_from_home
              median_dwell
              bucketed_dwell_times
              related_same_day_brand
              related_same_month_brand
              normalized_visits_by_total_visits
              normalized_visits_by_state_scaling
              normalized_visits_by_total_visitors
              normalized_visits_by_region_naics_visits
              normalized_visits_by_region_naics_visitors
            }
          }
        }
      }
    }
  }
}
"""



previous_curser = "NONE"
end_curser = ""
item = 0
first_run = True
while first_run or (end_curser != previous_curser and end_curser):
  query_sg_text = query_sg\
    .replace("--STATENAME--", "UT")\
    .replace("--FILTERS--", '')\
    .replace("--DATESTART--", "2021-06-01")\
    .replace("--DATEEND--", "2021-07-31")\
    .replace("--ENDCURSER--", end_curser)
  sgIter = client.execute(gql(query_sg_text))
  pageInformation = sgIter['search']['places']['results']['pageInfo']
  nextPaging = pageInformation['endCursor']
  edgesIter = sgIter['search']['places']['results']['edges']
  sgIter = [dat.pop('node') for dat in edgesIter]
  sgIter = [dat.pop('monthly_patterns') for dat in sgIter]
  
  previous_curser = end_curser
  end_curser = nextPaging
  

  with jsonlines.open("/tmp/safegraph/cgjde/section"+str(item)+".jl", 'w') as writer:
    writer.write_all(sgIter)
    writer.close()
  
  
  item += 1
  if first_run:
    first_run = False
  
  print(f'item number: {item}')
  

dbutils.fs.cp("file:/tmp/safegraph/cgjde", "dbfs:/FileStore/Team-CGJDE/safegraph/ut_jun_jul_2021", recurse = True)

In [0]:

dfsg = spark.read.json("dbfs:/FileStore/Team-CGJDE/safegraph/ut_jun_jul_2021", schema = schema)

In [0]:
display(dfsg)

placekey location_name parent_placekey street_address city date_range_end date_range_start poi_cbg postal_code iso_country_code median_dwell raw_visit_counts raw_visitor_counts visits_by_day region device_type bucketed_dwell_times distance_from_home related_same_day_brand related_same_month_brand visitor_country_of_origin visitor_daytime_cbgs visitor_home_aggregation visitor_home_cbgs normalized_visits_by_total_visits normalized_visits_by_state_scaling normalized_visits_by_total_visitors normalized_visits_by_region_naics_visits normalized_visits_by_region_naics_visitors null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 22b-222@5qb-szw-3bk CARQUEST Auto Parts null 95 N Main St Manti 2021-07-01T00:00:00-06:00 2021-06-01T00:00:00-06:00 490399725002 84642 null 10.0 46 37 List(1, 2, 3, 2, 2, 0, 2, 3, 1, 2, 1, 3, 2, 1, 1, 0, 3, 1, 2, 3, 0, 0, 0, 0, 3, 2, 0, 2, 2, 2) ut Map(android -> 25, ios -> 12) Map(5-10 -> 27, 21-60 -> 10, 61-120 -> 1, <5 -> 2, >240 -> 0, 11-20 -> 6, 121-240 -> 0) 1221 Map(Walmart -> 24, Chevrolet -> 2, Habitat for Humanity ReStore -> 2, Chevron -> 11, Miracle-Ear -> 2, Krispy Krunchy Chicken -> 2, NAPA Auto Parts -> 7, 7-Eleven -> 2, Wendy's -> 2, Hampton -> 4, Buick -> 2, Ace Hardware -> 2, Maverik -> 4, Sinclair Oil -> 9, McDonald's -> 4, Tractor Supply Co. -> 7, Phillips 66 -> 4, AutoZone -> 4, Subway -> 7, Dollar Tree -> 4) Map(Walmart -> 76, Chevron -> 57, NAPA Auto Parts -> 22, 7-Eleven -> 19, Wendy's -> 22, Ace Hardware -> 19, Denny's -> 16, Love's Travel Stops and Country Stores -> 22, Maverik -> 54, Sinclair Oil -> 46, Costco -> 19, McDonald's -> 57, Tractor Supply Co. -> 35, Phillips 66 -> 30, AutoZone -> 41, Intermountain Farmers Association (IFA) -> 16, Mountain America Credit Union -> 22, Exxon Mobil -> 22, Subway -> 41, Dollar Tree -> 24) Map(US -> 35) Map(271450112004 -> 4, 490399725002 -> 9, 490399725003 -> 6, 490399725001 -> 7, 490111251022 -> 4, 490211103001 -> 4) Map(49039972500 -> 28, 49039972300 -> 4, 47105060302 -> 4, 49021110300 -> 4) Map(490399725001 -> 10, 490399725002 -> 8, 490399725003 -> 5, 490399723003 -> 4) 3.322927753627156E-6 783.2880144612402 8.692620482069239E-6 4.331654032675738E-4 7.628903593876976E-4 22b-222@5qb-szw-3bk CARQUEST Auto Parts null 95 N Main St Manti 2021-08-01T00:00:00-06:00 2021-07-01T00:00:00-06:00 490399725002 84642 null 10.0 59 43 List(1, 5, 4, 0, 3, 1, 0, 2, 0, 3, 0, 0, 0, 1, 0, 7, 3, 4, 1, 3, 2, 1, 2, 2, 1, 4, 2, 5, 0, 1, 1) ut Map(android -> 27, ios -> 15) Map(5-10 -> 33, 21-60 -> 13, 61-120 -> 2, <5 -> 2, >240 -> 0, 11-20 -> 9, 121-240 -> 0) 4032 Map(Walmart -> 16, Little Caesars -> 2, TacoTime -> 2, Chevron -> 7, KFC -> 2, The Home Depot -> 2, 7-Eleven -> 4, Deseret Industries (D.I.) -> 2, Costco Gasoline -> 2, Hampton -> 2, Ace Hardware -> 2, Denny's -> 4, Staples -> 2, Smith's Food & Drug Stores -> 2, Maverik -> 2, Sinclair Oil -> 9, Costco -> 2, United States Postal Service (USPS) -> 2, McDonald's -> 4, Roxberry -> 4) Map(Walmart -> 84, Chevron -> 63, Taco Bell -> 16, NAPA Auto Parts -> 21, The Home Depot -> 21, Wendy's -> 16, Denny's -> 19, Maverik -> 58, Sinclair Oil -> 51, Costco -> 19, McDonald's -> 47, Tractor Supply Co. -> 26, Phillips 66 -> 26, AutoZone -> 16, Mountain America Credit Union -> 19, Exxon Mobil -> 26, Subway -> 53, Dollar Tree -> 30, Arby's -> 23, Family Dollar Stores -> 19) Map(US -> 42) Map(490399725002 -> 10, 490399725003 -> 5, 471050603021 -> 4, 490399725001 -> 6, 490230101002 -> 4, 490419752002 -> 4) Map(49039972500 -> 27, 49039972300 -> 5, 27145011200 -> 4, 49039972400 -> 4) Map(490399725002 -> 12, 490399725003 -> 7, 490399725001 -> 8, 490419752002 -> 4, 490490030012 -> 4) 4.17239693525423E-6 1027.6600154355726 9.776569019962617E-6 5.753291077523159E-4 9.791556027615507E-4 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null

In [0]:
dfsg.count()

Out[9]: 89966

In [0]:
spark.sql("DROP DATABASE IF EXISTS cgjde CASCADE")
spark.sql("CREATE DATABASE cgjde")
spark.sql("DROP DATABASE IF EXISTS cgjde CASCADE")
spark.sql("CREATE DATABASE cgjde")

Out[10]: DataFrame[]

In [0]:
dfsg = dfsg.na.drop(subset=["placekey"])
dfsg = dfsg.persist()
print("Count with all json files: " + str(dfsg.count()))

dfsg = dfsg.dropDuplicates(['placekey', 'date_range_start'])
dfsg.persist()
print("Count after duplicates: " + str(dfsg.count()))

dfsg.repartition(10).write.format("delta").saveAsTable("cgjde.test_table")

dfsg.unpersist()

print("done")

print(dfsg.limit(5).show())

Count with all json files: 60501
Count after duplicates: 60205
done
+-------------------+--------------------+---------------+--------------------+--------------+--------------------+--------------------+------------+-----------+----------------+------------+----------------+------------------+--------------------+------+--------------------+--------------------+------------------+----------------------+------------------------+-------------------------+--------------------+------------------------+--------------------+---------------------------------+----------------------------------+-----------------------------------+----------------------------------------+------------------------------------------+
 placekey| location_name|parent_placekey| street_address| city| date_range_end| date_range_start| poi_cbg|postal_code|iso_country_code|median_dwell|raw_visit_counts|raw_visitor_counts| visits_by_day|region| device_type|bucketed_dwell_times|distance_from_home|related_same_day_brand|related_same_month_brand|visitor_country_of_origin|visitor_daytime_cbgs|visitor_home_aggregation| visitor_home_cbgs|normalized_visits_by_total_visits|normalized_visits_by_state_scaling|normalized_visits_by_total_visitors|normalized_visits_by_region_naics_visits|normalized_visits_by_region_naics_visitors|
+-------------------+--------------------+---------------+--------------------+--------------+--------------------+--------------------+------------+-----------+----------------+------------+----------------+------------------+--------------------+------+--------------------+--------------------+------------------+----------------------+------------------------+-------------------------+--------------------+------------------------+--------------------+---------------------------------+----------------------------------+-----------------------------------+----------------------------------------+------------------------------------------+
222-222@5qb-9g4-d5f|Woodland Hills Fi...| null|690 S Woodland Hi...|Woodland Hills|2021-07-01T00:00:...|2021-06-01T00:00:...|490490104113| 84653| null| 76.5| 22| 10|[1, 1, 3, 0, 0, 1...| ut|{android -> 6, io...|{<5 -> 1, 5-10 ->...| 2177| {Walmart -> 10, C...| {Walmart -> 60, C...| {US -> 8}|{490490104113 -> ...| {49049010411 -> 4}|{490490104113 -> ...| 1.589226316952118E-6| 374.6160069162453| 2.34935688704574E-6| 6.958942240779402E-4| 0.002171767028627838|
222-222@5qb-9g4-d5f|Woodland Hills Fi...| null|690 S Woodland Hi...|Woodland Hills|2021-08-01T00:00:...|2021-07-01T00:00:...|490490104113| 84653| null| 23.0| 10| 7|[2, 0, 0, 0, 0, 0...| ut|{android -> 6, io...|{<5 -> 0, 5-10 ->...| 6064| {Walmart -> 10, V...| {Walmart -> 100, ...| {US -> 5}| {490490104061 -> 4}| {49049010411 -> 4...|{490490027021 -> ...| 7.071859212295304E-7| 174.1796636331479| 1.591534491621821...| 3.121196042323418E-4| 9.214042200313277E-4|
222-222@5qb-9g4-dqf| BragleBe| null| 670 S Oak Dr|Woodland Hills|2021-07-01T00:00:...|2021-06-01T00:00:...|490490104113| 84653| null| 104.0| 13| 9|[0, 2, 0, 1, 0, 0...| ut|{android -> 6, io...|{<5 -> 0, 5-10 ->...| 58336| {Lowe's -> 15, Ro...| {Walmart -> 56, C...| {US -> 8}| {490351135122 -> 4}| {49035112819 -> 4}| {}| 9.390882781989789E-7| 221.36400408687223| 2.114421198341166...| 5.594213001811664E-5| 8.640744433366567E-5|
222-222@5qb-9g4-dqf| BragleBe| null| 670 S Oak Dr|Woodland Hills|2021-08-01T00:00:...|2021-07-01T00:00:...|490490104113| 84653| null| 23.0| 9| 8|[0, 0, 0, 0, 0, 0...| ut|{android -> 4, io...|{<5 -> 0, 5-10 ->...| 42762| {Lowe's -> 22, Co...| {Walmart -> 50, L...| {US -> 9}| {490490104113 -> 4}| {}|{490490104113 -> ...| 6.364673291065774E-7| 156.76169726983312| 1.818896561853510...| 3.735230276946574E-5| 5.745328728558752...|
222-222@5qb-9g9-rc5|Aren Bybee Real E...| null| 1225 N Washougal| Elk Ridge|2021-07-01T00:00:...|2021-06-01T00:00:...|490490104112| 84651| null| 123.5| 54| 30|[1, 1, 3, 6, 2, 1...| ut|{android -> 10, i...|{<5 -> 3, 5-10 ->...| 9505| {Chevron -> 7, Wa...| {Walmart -

In [0]:
dfsg.count()

Out[12]: 60205

#Part 2

Use the data from the created table to create two visualizations (Team).

In [0]:
new_df = dfsg.filter(dfsg['location_name'].like('%Target%'))
new_df.count()

Out[61]: 22

In [0]:
new_df = dfsg.filter(dfsg['location_name'].like('%Walmart%'))
new_df.count()

Out[62]: 128

In [0]:
target_df = spark.sql("""SELECT placekey, location_name, visits_by_day, right(left(date_range_start, 7), 1) as month FROM cgjde.test_table
WHERE location_name LIKE 'Target'""")

for x in target_df.collect():
 
  index = 1
  for y in x.visits_by_day:
    print(f'{x.placekey}: count= {y} on the {index} of {x.month}')
    index += 1

zzw-222@5qd-3rp-ffz: count= 93 on the 1 of 6
zzw-222@5qd-3rp-ffz: count= 84 on the 2 of 6
zzw-222@5qd-3rp-ffz: count= 86 on the 3 of 6
zzw-222@5qd-3rp-ffz: count= 87 on the 4 of 6
zzw-222@5qd-3rp-ffz: count= 108 on the 5 of 6
zzw-222@5qd-3rp-ffz: count= 61 on the 6 of 6
zzw-222@5qd-3rp-ffz: count= 88 on the 7 of 6
zzw-222@5qd-3rp-ffz: count= 76 on the 8 of 6
zzw-222@5qd-3rp-ffz: count= 72 on the 9 of 6
zzw-222@5qd-3rp-ffz: count= 83 on the 10 of 6
zzw-222@5qd-3rp-ffz: count= 72 on the 11 of 6
zzw-222@5qd-3rp-ffz: count= 103 on the 12 of 6
zzw-222@5qd-3rp-ffz: count= 55 on the 13 of 6
zzw-222@5qd-3rp-ffz: count= 89 on the 14 of 6
zzw-222@5qd-3rp-ffz: count= 83 on the 15 of 6
zzw-222@5qd-3rp-ffz: count= 82 on the 16 of 6
zzw-222@5qd-3rp-ffz: count= 77 on the 17 of 6
zzw-222@5qd-3rp-ffz: count= 84 on the 18 of 6
zzw-222@5qd-3rp-ffz: count= 116 on the 19 of 6
zzw-222@5qd-3rp-ffz: count= 61 on the 20 of 6
zzw-222@5qd-3rp-ffz: count= 96 on the 21 of 6
zzw-222@5qd-3rp-ffz: count= 76 on the 22 of 6
zzw-222@5qd-3rp-ffz: count= 72 on the 23 of 6
zzw-222@5qd-3rp-ffz: count= 75 on the 24 of 6
zzw-222@5qd-3rp-ffz: count= 92 on the 25 of 6
zzw-222@5qd-3rp-ffz: count= 122 on the 26 of 6
zzw-222@5qd-3rp-ffz: count= 58 on the 27 of 6
zzw-222@5qd-3rp-ffz: count= 76 on the 28 of 6
zzw-222@5qd-3rp-ffz: count= 68 on the 29 of 6
zzw-222@5qd-3rp-ffz: count= 74 on the 30 of 6
222-222@5qc-x6g-4sq: count= 168 on the 1 of 6
222-222@5qc-x6g-4sq: count= 152 on the 2 of 6
222-222@5qc-x6g-4sq: count= 136 on the 3 of 6
222-222@5qc-x6g-4sq: count= 168 on the 4 of 6
222-222@5qc-x6g-4sq: count= 202 on the 5 of 6
222-222@5qc-x6g-4sq: count= 113 on the 6 of 6
222-222@5qc-x6g-4sq: count= 146 on the 7 of 6
222-222@5qc-x6g-4sq: count= 140 on the 8 of 6
222-222@5qc-x6g-4sq: count= 138 on the 9 of 6
222-222@5qc-x6g-4sq: count= 125 on the 10 of 6
222-222@5qc-x6g-4sq: count= 162 on the 11 of 6
222-222@5qc-x6g-4sq: count= 191 on the 12 of 6
222-222@5qc-x6g-4sq: count= 85 on the 13 of 6
222-222@5qc-x6g-4sq: count= 130 on the 14 of 6
222-222@5qc-x6g-4sq: count= 135 on the 15 of 6
222-222@5qc-x6g-4sq: count= 146 on the 16 of 6
222-222@5qc-x6g-4sq: count= 134 on the 17 of 6
222-222@5qc-x6g-4sq: count= 171 on the 18 of 6
222-222@5qc-x6g-4sq: count= 227 on the 19 of 6
222-222@5qc-x6g-4sq: count= 89 on the 20 of 6
222-222@5qc-x6g-4sq: count= 155 on the 21 of 6
222-222@5qc-x6g-4sq: count= 120 on the 22 of 6
222-222@5qc-x6g-4sq: count= 130 on the 23 of 6
222-222@5qc-x6g-4sq: count= 164 on the 24 of 6
222-222@5qc-x6g-4sq: count= 154 on the 25 of 6
222-222@5qc-x6g-4sq: count= 182 on the 26 of 6
222-222@5qc-x6g-4sq: count= 88 on the 27 of 6
222-222@5qc-x6g-4sq: count= 190 on the 28 of 6
222-222@5qc-x6g-4sq: count= 147 on the 29 of 6
222-222@5qc-x6g-4sq: count= 150 on the 30 of 6
zzw-223@5qc-x6w-6hq: count= 27 on the 1 of 7
zzw-223@5qc-x6w-6hq: count= 32 on the 2 of 7
zzw-223@5qc-x6w-6hq: count= 41 on the 3 of 7
zzw-223@5qc-x6w-6hq: count= 17 on the 4 of 7
zzw-223@5qc-x6w-6hq: count= 42 on the 5 of 7
zzw-223@5qc-x6w-6hq: count= 33 on the 6 of 7
zzw-223@5qc-x6w-6hq: count= 31 on the 7 of 7
zzw-223@5qc-x6w-6hq: count= 30 on the 8 of 7
zzw-223@5qc-x6w-6hq: count= 36 on the 9 of 7
zzw-223@5qc-x6w-6hq: count= 40 on the 10 of 7
zzw-223@5qc-x6w-6hq: count= 12 on the 11 of 7
zzw-223@5qc-x6w-6hq: count= 29 on the 12 of 7
zzw-223@5qc-x6w-6hq: count= 32 on the 13 of 7
zzw-223@5qc-x6w-6hq: count= 29 on the 14 of 7
zzw-223@5qc-x6w-6hq: count= 31 on the 15 of 7
zzw-223@5qc-x6w-6hq: count= 33 on the 16 of 7
zzw-223@5qc-x6w-6hq: count= 29 on the 17 of 7
zzw-223@5qc-x6w-6hq: count= 16 on the 18 of 7
zzw-223@5qc-x6w-6hq: count= 38 on the 19 of 7
zzw-223@5qc-x6w-6hq: count= 30 on the 20 of 7
zzw-223@5qc-x6w-6hq: count= 39 on the 21 of 7
zzw-223@5qc-x6w-6hq: count= 27 on the 22 of 7
zzw-223@5qc-x6w-6hq: count= 26 on the 23 of 7
zzw-223@5qc-x6w-6hq: count= 35 on the 24 of 7
zzw-223@5qc-x6w-6hq: count= 11 on the 25 of 7
zzw-223@5qc-x6w-6hq: count= 44 on the 26 of 7
zzw-223@5qc-x6w-6hq: count= 25 on the 27

In [0]:
display(target_df)

placekey location_name visits_by_day month zzw-222@5qd-3rp-ffz Target List(93, 84, 86, 87, 108, 61, 88, 76, 72, 83, 72, 103, 55, 89, 83, 82, 77, 84, 116, 61, 96, 76, 72, 75, 92, 122, 58, 76, 68, 74) 6 222-222@5qc-x6g-4sq Target List(168, 152, 136, 168, 202, 113, 146, 140, 138, 125, 162, 191, 85, 130, 135, 146, 134, 171, 227, 89, 155, 120, 130, 164, 154, 182, 88, 190, 147, 150) 6 zzw-223@5qc-x6w-6hq Target List(27, 32, 41, 17, 42, 33, 31, 30, 36, 40, 12, 29, 32, 29, 31, 33, 29, 16, 38, 30, 39, 27, 26, 35, 11, 44, 25, 25, 28, 35, 32) 7 zzw-224@5qc-w8d-94v Target List(60, 59, 50, 39, 59, 52, 45, 71, 58, 81, 49, 46, 53, 49, 43, 57, 81, 53, 47, 53, 61, 60, 72, 78, 34, 52, 59, 65, 51, 63, 99) 7 zzw-225@5qd-38t-2kz Target List(1, 5, 2, 4, 3, 4, 3, 3, 5, 3, 7, 8, 4, 8, 6, 4, 2, 1, 3, 4, 2, 3, 3, 4, 1, 3, 3, 4, 3, 9, 22) 7 zzw-222@5qd-3rp-ffz Target List(79, 85, 97, 63, 98, 64, 100, 69, 88, 95, 67, 91, 68, 75, 74, 101, 97, 54, 83, 93, 93, 97, 93, 103, 57, 70, 87, 75, 87, 88, 112) 7 222-222@5yz-n7r-249 Target List(138, 117, 129, 131, 171, 100, 128, 111, 112, 120, 137, 145, 110, 115, 106, 134, 135, 127, 157, 90, 135, 97, 144, 133, 120, 138, 102, 124, 107, 120) 6 zzw-222@5qc-xmm-zpv Target List(103, 106, 131, 80, 103, 95, 99, 98, 119, 125, 101, 82, 70, 87, 81, 122, 98, 93, 93, 81, 73, 89, 103, 134, 64, 71, 65, 105, 102, 122, 129) 7 zzw-223@5qc-x6w-6hq Target List(34, 29, 34, 41, 37, 14, 35, 31, 35, 26, 38, 31, 16, 27, 28, 37, 30, 32, 49, 22, 38, 32, 38, 30, 47, 28, 20, 42, 26, 26) 6 222-224@5qc-xjv-5pv Target List(112, 113, 122, 146, 148, 99, 107, 110, 135, 103, 122, 131, 98, 104, 97, 107, 99, 163, 180, 108, 92, 98, 102, 110, 144, 147, 82, 92, 108, 101) 6 222-222@5yz-n7r-249 Target List(131, 149, 145, 83, 116, 89, 104, 108, 145, 152, 100, 109, 99, 112, 139, 152, 176, 96, 134, 113, 125, 117, 124, 132, 77, 122, 117, 120, 139, 129, 158) 7 zzw-222@5qc-xmm-zpv Target List(93, 120, 117, 111, 153, 114, 131, 100, 93, 112, 108, 146, 83, 82, 106, 81, 78, 119, 147, 97, 116, 94, 86, 88, 126, 118, 96, 101, 96, 91) 6 zzw-223@5qc-xtb-p5f Target List(122, 144, 125, 143, 159, 81, 115, 116, 105, 103, 130, 122, 94, 115, 140, 124, 142, 135, 152, 74, 106, 118, 96, 95, 98, 120, 96, 92, 102, 130) 6 zzw-224@5qc-w8d-94v Target List(51, 60, 61, 52, 73, 35, 58, 43, 40, 58, 50, 55, 49, 49, 45, 59, 49, 80, 79, 47, 52, 46, 55, 55, 66, 60, 48, 53, 49, 61) 6 222-223@5qc-w72-975 Target List(78, 79, 107, 58, 88, 81, 84, 78, 79, 131, 47, 94, 88, 93, 76, 92, 101, 91, 67, 88, 77, 88, 105, 114, 71, 76, 86, 79, 94, 98, 138) 7 222-224@5qc-xjv-5pv Target List(128, 118, 168, 87, 116, 125, 108, 119, 128, 111, 100, 114, 89, 77, 120, 123, 152, 91, 93, 122, 99, 105, 108, 132, 86, 105, 126, 116, 122, 137, 175) 7 222-222@5qc-x6g-4sq Target List(148, 192, 170, 65, 172, 148, 144, 169, 173, 170, 103, 154, 142, 128, 132, 153, 202, 73, 159, 140, 129, 139, 167, 150, 67, 151, 129, 134, 151, 164, 174) 7 zzw-223@5qc-xtb-p5f Target List(105, 134, 106, 63, 99, 103, 113, 119, 102, 133, 88, 116, 110, 116, 102, 129, 145, 64, 102, 116, 119, 116, 135, 138, 86, 140, 109, 113, 128, 127, 158) 7 zzw-222@5qc-w8h-2hq Target List(4, 3, 7, 8, 5, 32, 5, 4, 8, 4, 3, 2, 8, 8, 2, 7, 10, 10, 45, 6, 6, 9, 13, 12, 4, 53, 5, 17, 5, 3) 6 zzw-225@5qd-38t-2kz Target List(6, 3, 4, 5, 5, 4, 3, 4, 6, 0, 6, 1, 3, 4, 3, 2, 2, 8, 4, 4, 4, 5, 5, 7, 4, 4, 3, 4, 2, 3) 6 222-223@5qc-w72-975 Target List(84, 83, 87, 98, 128, 52, 74, 73, 64, 86, 92, 110, 64, 67, 88, 98, 93, 112, 129, 61, 81, 103, 71, 95, 92, 106, 69, 76, 86, 84) 6 zzw-222@5qc-w8h-2hq Target List(4, 14, 48, 9, 2, 3, 4, 3, 4, 45, 2, 4, 4, 4, 6, 3, 57, 39, 5, 5, 2, 6, 3, 54, 3, 7, 4, 3, 3, 3, 5) 7

In [0]:
%sql

SELECT visits_by_day
FROM cgjde.test_table

visits_by_day List(4, 4, 5, 1, 7, 2, 8, 10, 4, 6, 0, 2, 6, 7, 4, 7, 7, 2, 9, 6, 7, 3, 6, 4, 2, 4, 3, 2, 5, 6, 2) List(3, 0, 0, 3, 2, 2, 0, 3, 0, 1, 1, 0, 0, 3, 0, 4, 0, 3, 2, 1, 3, 0, 3, 2, 0, 0, 1, 2, 0, 1) List(1, 3, 2, 0, 0, 0, 3, 1, 1, 4, 1, 0, 0, 4, 1, 1, 3, 7, 1, 0, 9, 1, 1, 2, 5, 0, 0, 0, 2, 4) List(66, 80, 69, 33, 71, 60, 65, 74, 62, 87, 31, 59, 60, 51, 52, 88, 70, 36, 56, 48, 43, 71, 67, 51, 28, 48, 50, 61, 73, 83, 75) List(13, 13, 0, 2, 0, 5, 1, 2, 2, 1, 4, 7, 3, 0, 10, 1, 2, 0, 2, 4, 1, 1, 1, 2, 1, 1, 7, 2, 1, 1) List(2, 3, 5, 4, 2, 13, 7, 4, 8, 6, 1, 5, 15, 5, 4, 1, 1, 6, 2, 13, 11, 4, 4, 6, 6, 3, 12, 8, 8, 4) List(1, 2, 0, 1, 0, 1, 3, 4, 16, 21, 0, 1, 2, 2, 9, 5, 4, 0, 9, 12, 0, 2, 6, 2, 0, 2, 3, 0, 2, 3, 6) List(7, 8, 7, 1, 2, 4, 6, 10, 5, 7, 14, 7, 3, 6, 6, 9, 5, 5, 3, 2, 6, 6, 16, 9, 12, 7, 8, 10, 15, 5, 6) List(0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 2, 0, 1, 0, 2, 0, 1, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0) List(0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0) List(2, 0, 0, 0, 2, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 2, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0) List(8, 14, 5, 10, 17, 7, 8, 9, 3, 14, 11, 13, 9, 6, 19, 13, 13, 7, 21, 17, 20, 1, 13, 13, 11, 10, 13, 9, 8, 11) List(8, 5, 3, 4, 4, 3, 6, 9, 2, 3, 2, 1, 1, 1, 0, 0, 0, 1, 2, 2, 1, 2, 1, 2, 3, 1, 1, 2, 1, 3) List(1, 2, 5, 4, 0, 0, 0, 0, 5, 3, 0, 0, 0, 0, 2, 0, 0, 0, 4, 4, 7, 6, 2, 0, 1, 0, 2, 3, 0, 0, 0) List(2, 2, 5, 8, 6, 8, 0, 4, 4, 2, 5, 10, 6, 0, 1, 5, 5, 7, 1, 18, 2, 2, 4, 12, 7, 12, 10, 0, 1, 5) List(0, 2, 1, 0, 0, 12, 2, 3, 1, 0, 1, 0, 5, 0, 7, 4, 3, 4, 1, 0, 2, 1, 2, 1, 0, 0, 2, 2, 1, 1) List(1, 1, 1, 0, 3, 1, 2, 2, 2, 2, 1, 2, 3, 1, 1, 3, 4, 1, 0, 2, 1, 2, 2, 2, 1, 1, 1, 2, 2, 3, 3) List(0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 1, 3, 0, 0, 0, 0, 0, 0, 0) List(0, 1, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0) List(23, 29, 39, 35, 33, 23, 31, 23, 31, 23, 21, 16, 28, 26, 30, 27, 31, 32, 22, 26, 31, 19, 35, 37, 32, 19, 22, 25, 27, 40, 32) List(2, 1, 0, 7, 4, 5, 7, 5, 5, 8, 8, 9, 7, 3, 9, 7, 1, 4, 9, 8, 8, 11, 12, 15, 8, 9, 12, 10, 6, 11, 11) List(11, 6, 5, 11, 11, 4, 2, 4, 2, 3, 1, 4, 3, 1, 3, 2, 3, 1, 4, 7, 6, 3, 3, 2, 2, 3, 3, 1, 2, 15) List(0, 3, 1, 3, 1, 5, 5, 2, 3, 2, 2, 2, 2, 2, 4, 4, 3, 3, 1, 5, 0, 2, 2, 0, 2, 4, 5, 1, 4, 5, 3) List(1, 5, 9, 0, 2, 8, 7, 5, 5, 3, 3, 2, 3, 5, 7, 4, 5, 2, 5, 8, 4, 2, 10, 4, 3, 7, 4, 6, 6, 7, 4) List(1, 0, 4, 4, 1, 1, 0, 0, 2, 2, 2, 1, 0, 2, 1, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 1, 2, 0, 1) List(1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 2, 1, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0) List(0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0) List(0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0) List(9, 10, 1, 9, 1, 6, 8, 9, 15, 9, 10, 14, 15, 17, 6, 4, 5, 6, 9, 11, 3, 5, 3, 9, 10, 8, 12, 8, 12, 10, 10) List(108, 113, 105, 103, 119, 110, 100, 97, 109, 120, 128, 95, 69, 90, 125, 116, 132, 147, 78, 87, 96, 109, 109, 131, 132, 110, 81, 78, 96, 115, 120) List(4, 5, 1, 1, 2, 2, 1, 3, 1, 0, 5, 4, 3, 3, 4, 1, 4, 1, 6, 3, 4, 2, 3, 4, 4, 3, 6, 2, 2, 2, 5) List(1, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 0, 0, 0, 1, 0, 1, 2, 0) List(28, 20, 23, 26, 21, 18, 24, 22, 30, 25, 43, 33, 14, 27, 27, 37, 21, 28, 30, 12, 35, 33, 25, 28, 30, 26, 20, 31, 32, 37) List(0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 1, 0, 0, 1, 0) List(2, 1, 1, 0, 0, 0, 1, 1, 1, 0, 1, 0, 0, 0, 3, 3, 0, 0, 0, 0, 0, 1, 1, 0, 2, 1, 0, 0, 0, 1) List(17, 21, 5, 7, 16, 16, 24, 18, 13, 5, 3, 14, 8, 8, 16, 10, 14, 0, 12, 11, 17, 11, 14, 12, 1, 12, 10, 15, 9, 16, 21) List(1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0) List(6, 4, 3, 4, 37, 2, 1, 0, 2, 3, 2, 4, 5, 1, 1, 6, 2, 3, 7, 3, 6, 5, 5, 3, 2, 3, 1, 4, 4, 5, 2) List(0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

In [0]:


temp_jun = spark.sql("""SELECT placekey, location_name, visits_by_day, right(left(date_range_start, 7), 1) as month 
FROM cgjde.test_table
WHERE right(left(date_range_start, 7), 1) == '6'
AND location_name == "Smith\'s Food & Drug Stores" """)

temp_jul = spark.sql("""SELECT placekey, location_name, visits_by_day, right(left(date_range_start, 7), 1) as month 
FROM cgjde.test_table
WHERE right(left(date_range_start, 7), 1) == '7'
AND location_name == "Smith\'s Food & Drug Stores" """)


temp_jun = temp_jun.select('placekey', *[F.col('visits_by_day')[i].alias(f'6/{i+1}') for i in range(30)])
temp_jul = temp_jul.select('placekey', *[F.col('visits_by_day')[i].alias(f'7/{i+1}') for i in range(31)])
                     
compiled_junjul = temp_jun.join(temp_jul, temp_jun.placekey == temp_jul.placekey) 
compiled_junjul = compiled_junjul.drop('placekey')
                                         
compiled_junjul = compiled_junjul.groupBy().sum()
display(compiled_junjul)

sum(6/1) sum(6/2) sum(6/3) sum(6/4) sum(6/5) sum(6/6) sum(6/7) sum(6/8) sum(6/9) sum(6/10) sum(6/11) sum(6/12) sum(6/13) sum(6/14) sum(6/15) sum(6/16) sum(6/17) sum(6/18) sum(6/19) sum(6/20) sum(6/21) sum(6/22) sum(6/23) sum(6/24) sum(6/25) sum(6/26) sum(6/27) sum(6/28) sum(6/29) sum(6/30) sum(7/1) sum(7/2) sum(7/3) sum(7/4) sum(7/5) sum(7/6) sum(7/7) sum(7/8) sum(7/9) sum(7/10) sum(7/11) sum(7/12) sum(7/13) sum(7/14) sum(7/15) sum(7/16) sum(7/17) sum(7/18) sum(7/19) sum(7/20) sum(7/21) sum(7/22) sum(7/23) sum(7/24) sum(7/25) sum(7/26) sum(7/27) sum(7/28) sum(7/29) sum(7/30) sum(7/31) 1516 1466 1577 1668 1897 1472 1548 1430 1459 1434 1465 1840 1382 1450 1459 1374 1540 1618 2184 1607 1513 1455 1488 1509 1570 1771 1398 1476 1492 1583 1633 1883 2026 1543 1701 1549 1449 1484 1610 1835 1421 1610 1479 1492 1481 1558 1876 1486 1606 1445 1429 1544 1645 1831 1355 1537 1600 1435 1434 1655 1781

In [0]:
compiled_junjul = compiled_junjul.toPandas().transpose().reset_index()
compiled_junjul = compiled_junjul.rename(columns={0: "visits"})
compiled_junjul['index'] = compiled_junjul['index'].map(lambda x: x.lstrip('sum\(').rstrip('\)'))
compiled_junjul.columns = ['Day', 'Visits']

compiled_junjul

Out[66]:

Day 
 Visits 
 
 
 
 
 0 
 6/1 
 1516 
 
 
 1 
 6/2 
 1466 
 
 
 2 
 6/3 
 1577 
 
 
 3 
 6/4 
 1668 
 
 
 4 
 6/5 
 1897 
 
 
 ... 
 ... 
 ... 
 
 
 56 
 7/27 
 1600 
 
 
 57 
 7/28 
 1435 
 
 
 58 
 7/29 
 1434 
 
 
 59 
 7/30 
 1655 
 
 
 60 
 7/31 
 1781 
 
 
 
 61 rows × 2 columns

In [0]:
visiteschart = alt.Chart(compiled_junjul, width = 500).mark_line().encode(
  x = alt.X("Day", sort=alt.EncodingSortField(field="Letters", op="count", order='ascending')),
  y = "Visits"
).properties(
    title={
        "text":["Distribution of Visits for Smith's"],
        "subtitle":[""]
    },
  width=900
)
visiteschart

Out[67]:

In [0]:

# %sql
# Select location_name from cgjde.test_table
# where Contains (location_name, "Walmart") OR location_name == "Target"

In [0]:


temp_jun_target = spark.sql("""SELECT placekey, location_name, visits_by_day, right(left(date_range_start, 7), 1) as month 
FROM cgjde.test_table
WHERE right(left(date_range_start, 7), 1) == '6'
AND location_name == "Target" """)

temp_jun_walmart = spark.sql("""SELECT placekey, location_name, visits_by_day, right(left(date_range_start, 7), 1) as month 
FROM cgjde.test_table
WHERE right(left(date_range_start, 7), 1) == '6'
AND Contains (location_name, "Walmart") """)



temp_jul_walmart = spark.sql("""SELECT placekey, location_name, visits_by_day, right(left(date_range_start, 7), 1) as month 
FROM cgjde.test_table
WHERE right(left(date_range_start, 7), 1) == '7'
AND Contains (location_name, "Walmart") """)

temp_jul_target = spark.sql("""SELECT placekey, location_name, visits_by_day, right(left(date_range_start, 7), 1) as month 
FROM cgjde.test_table
WHERE right(left(date_range_start, 7), 1) == '7'
AND location_name == "Target" """)


temp_jun_target = temp_jun_target.select('placekey', *[F.col('visits_by_day')[i].alias(f'6/{i+1}') for i in range(30)])
temp_jul_target = temp_jul_target.select('placekey', *[F.col('visits_by_day')[i].alias(f'7/{i+1}') for i in range(31)])
                     
compiled_junjul_target = temp_jun_target.join(temp_jul_target, temp_jun_target.placekey == temp_jul_target.placekey) 
compiled_junjul_target = compiled_junjul_target.drop('placekey')
                                         
compiled_junjul_target = compiled_junjul_target.groupBy().mean()

                     
                     
compiled_junjul_target = compiled_junjul_target.toPandas().transpose().reset_index()
compiled_junjul_target = compiled_junjul_target.rename(columns={0: "visits"})
compiled_junjul_target['index'] = compiled_junjul_target['index'].map(lambda x: x.lstrip('avg\(').rstrip('\)'))
compiled_junjul_target.columns = ['Day', 'Mean Visits']
compiled_junjul_target['Brand'] = "Target"


temp_jun_walmart = temp_jun_walmart.select('placekey', *[F.col('visits_by_day')[i].alias(f'6/{i+1}') for i in range(30)])
temp_jul_walmart = temp_jul_walmart.select('placekey', *[F.col('visits_by_day')[i].alias(f'7/{i+1}') for i in range(31)])
                     
compiled_junjul_walmart = temp_jun_walmart.join(temp_jul_walmart, temp_jun_walmart.placekey == temp_jul_walmart.placekey) 
compiled_junjul_walmart = compiled_junjul_walmart.drop('placekey')
                                         
compiled_junjul_walmart = compiled_junjul_walmart.groupBy().mean()
# display(compiled_junjul_walmart)
                     
                     
compiled_junjul_walmart = compiled_junjul_walmart.toPandas().transpose().reset_index()
compiled_junjul_walmart = compiled_junjul_walmart.rename(columns={0: "visits"})
compiled_junjul_walmart['index'] = compiled_junjul_walmart['index'].map(lambda x: x.lstrip('avg\(').rstrip('\)'))
compiled_junjul_walmart.columns = ['Day', 'Mean Visits']
compiled_junjul_walmart['Brand'] = "Walmart"

compiled_junjul_walmart


Out[69]:

Day 
 Mean Visits 
 Brand 
 
 
 
 
 0 
 6/1 
 123.303571 
 Walmart 
 
 
 1 
 6/2 
 129.232143 
 Walmart 
 
 
 2 
 6/3 
 127.428571 
 Walmart 
 
 
 3 
 6/4 
 142.553571 
 Walmart 
 
 
 4 
 6/5 
 159.571429 
 Walmart 
 
 
 ... 
 ... 
 ... 
 ... 
 
 
 56 
 7/27 
 119.071429 
 Walmart 
 
 
 57 
 7/28 
 122.267857 
 Walmart 
 
 
 58 
 7/29 
 125.178571 
 Walmart 
 
 
 59 
 7/30 
 132.892857 
 Walmart 
 
 
 60 
 7/31 
 148.535714 
 Walmart 
 
 
 
 61 rows × 3 columns

In [0]:
walmart_chart = alt.Chart(compiled_junjul_walmart, width = 500).mark_line().encode(
  x = alt.X("Day", sort=alt.EncodingSortField(field="Letters", op="count", order='ascending')),
  y = "Mean Visits",
  color = "Brand"

).properties(
    title={
        "text":["Target vs. Walmart"],
        "subtitle":[""]
    }
)

target_chart = alt.Chart(compiled_junjul_target, width = 900).mark_line().encode(
  x = alt.X("Day", sort=alt.EncodingSortField(field="Letters", op="count", order='ascending')),
  y = "Mean Visits",
  color="Brand"
).properties(
    title={
        "text":["Target vs. Walmart"],
        "subtitle":[""]
    },
)

combine_chart = target_chart + walmart_chart

combine_chart

Out[70]:

Charting Stuff

In [0]:
pdf_sg = new_df.toPandas()

In [0]:
pdf_sg.columns

Out[72]: Index(['placekey', 'location_name', 'parent_placekey', 'street_address',
 'city', 'date_range_end', 'date_range_start', 'poi_cbg', 'postal_code',
 'iso_country_code', 'median_dwell', 'raw_visit_counts',
 'raw_visitor_counts', 'visits_by_day', 'region', 'device_type',
 'bucketed_dwell_times', 'distance_from_home', 'related_same_day_brand',
 'related_same_month_brand', 'visitor_country_of_origin',
 'visitor_daytime_cbgs', 'visitor_home_aggregation', 'visitor_home_cbgs',
 'normalized_visits_by_total_visits',
 'normalized_visits_by_state_scaling',
 'normalized_visits_by_total_visitors',
 'normalized_visits_by_region_naics_visits',
 'normalized_visits_by_region_naics_visitors'],
 dtype='object')

In [0]:
pdf_sg['location_name'].value_counts()

Out[73]: Walmart Supercenter 66
Walmart Neighborhood Market 14
Walmart Vision & Glasses 8
Walmart Distribution 6
Walmart Fuel Station 3
Walmart Center 2
Walmart Pharmacy 10 1573 2
Walmart Pharmacy 10 5235 2
Walmart Pharmacy 10 3220 2
Walmart Pharmacy 10 2511 2
Walmart Pharmacy 10 1572 2
Walmart Pharmacy 10 3208 2
Walmart Pickup 2
Cedar City Walmart Center 2
Walmart Pharmacy 10 3589 2
Walmart Pharmacy 10 5270 2
Walmart Pharmacy 10 5233 2
Walmart Pharmacy 10 5206 2
Walmart Pharmacy 10 1439 1
Walmart Pharmacy 10 1440 1
Walmart Pharmacy 10 5109 1
Walmart Pharmacy 10 2921 1
Walmart Pharmacy 10 1686 1
Name: location_name, dtype: int64

In [0]:
pdf_sg.head()

Out[74]:

placekey 
 location_name 
 parent_placekey 
 street_address 
 city 
 date_range_end 
 date_range_start 
 poi_cbg 
 postal_code 
 iso_country_code 
 median_dwell 
 raw_visit_counts 
 raw_visitor_counts 
 visits_by_day 
 region 
 device_type 
 bucketed_dwell_times 
 distance_from_home 
 related_same_day_brand 
 related_same_month_brand 
 visitor_country_of_origin 
 visitor_daytime_cbgs 
 visitor_home_aggregation 
 visitor_home_cbgs 
 normalized_visits_by_total_visits 
 normalized_visits_by_state_scaling 
 normalized_visits_by_total_visitors 
 normalized_visits_by_region_naics_visits 
 normalized_visits_by_region_naics_visitors 
 
 
 
 
 0 
 222-222@5qc-w95-8d9 
 Walmart Neighborhood Market 
 None 
 3555 S 8400 W 
 Magna 
 2021-07-01T00:00:00-06:00 
 2021-06-01T00:00:00-06:00 
 490351139054 
 84044 
 None 
 13.0 
 1686 
 808 
 [47, 46, 57, 61, 62, 56, 48, 80, 48, 39, 60, 5... 
 ut 
 {'android': 533, 'ios': 273} 
 {'<5': 38, '5-10': 661, '11-20': 443, '21-60':... 
 1962.0 
 {'Holiday Oil': 8, '7-Eleven': 7, 'Chevron': 6... 
 {'McDonald's': 55, 'Chevron': 52, 'Holiday Oil... 
 {'US': 795} 
 {'490351139071': 43, '490351139062': 39, '4903... 
 {'49035113905': 117, '49035113907': 117, '4903... 
 {'490351139071': 58, '490351139054': 46, '4903... 
 1.217925e-04 
 28709.208530 
 1.898280e-04 
 0.004369 
 0.007977 
 
 
 1 
 222-222@5ws-h5c-nbk 
 Walmart Supercenter 
 None 
 1550 N Main St 
 North Logan 
 2021-07-01T00:00:00-06:00 
 2021-06-01T00:00:00-06:00 
 490050004011 
 84341 
 None 
 20.0 
 3636 
 1984 
 [124, 130, 137, 156, 159, 80, 119, 118, 103, 9... 
 ut 
 {'android': 1387, 'ios': 590} 
 {'<5': 88, '5-10': 960, '11-20': 903, '21-60':... 
 13726.0 
 {'Build A Bear Workshop': 18, 'Maverik': 9, 'S... 
 {'Maverik': 55, 'McDonald's': 49, 'Build A Bea... 
 {'US': 1930} 
 {'490050004011': 90, '490050005021': 52, '4900... 
 {'49005000202': 138, '49005000403': 100, '4900... 
 {'490050004011': 63, '490050002022': 59, '4900... 
 2.626558e-04 
 61913.809143 
 4.661124e-04 
 0.009422 
 0.017204 
 
 
 2 
 222-223@5qc-zzt-35z 
 Walmart Pharmacy 10 5206 
 None 
 1710 E Skyline Dr 
 South Ogden 
 2021-07-01T00:00:00-06:00 
 2021-06-01T00:00:00-06:00 
 490572112022 
 84405 
 None 
 14.0 
 1 
 1 
 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ... 
 ut 
 {'android': 0, 'ios': 0} 
 {'<5': 0, '5-10': 0, '11-20': 1, '21-60': 0, '... 
 NaN 
 {'Advance Auto Parts': 100, 'Big O Tires': 100} 
 {'Hallmark Cards': 100, 'Walmart': 100, 'Advan... 
 {} 
 {} 
 {} 
 {} 
 7.223756e-08 
 17.028000 
 2.349357e-07 
 0.000005 
 0.000007 
 
 
 3 
 222-226@5qd-2fp-nyv 
 Walmart Pharmacy 10 2921 
 None 
 534 N Harrisville Rd 
 Harrisville 
 2021-08-01T00:00:00-06:00 
 2021-07-01T00:00:00-06:00 
 490572103021 
 84404 
 None 
 19.0 
 1 
 1 
 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ... 
 ut 
 {'android': 0, 'ios': 0} 
 {'<5': 0, '5-10': 0, '11-20': 1, '21-60': 0, '... 
 NaN 
 {'Walgreens': 100} 
 {'Walmart': 100, 'Taco Bell': 100, 'Starbucks'... 
 {'US': 4} 
 {} 
 {} 
 {} 
 7.071859e-08 
 17.417966 
 2.273621e-07 
 0.000004 
 0.000007 
 
 
 4 
 zzw-222@5qc-xty-hnq 
 Walmart Neighborhood Market 
 None 
 1202 W 12600 S 
 Riverton 
 2021-07-01T00:00:00-06:00 
 2021-06-01T00:00:00-06:00 
 490351146003 
 84065 
 None 
 16.0 
 1448 
 730 
 [47, 52, 47, 56, 53, 44, 56, 37, 36, 38, 45, 6... 
 ut 
 {'android': 422, 'ios': 307} 
 {'<5': 39, '5-10': 494, '11-20': 344, '21-60':... 
 3052.0 
 {'Sinclair Oil': 4, 'Vasa Fitness': 3, 'McDona... 
 {'McDonald's': 42, 'Sinclair Oil': 38, 'Maveri... 
 {'US': 694} 
 {'490351146003': 50, '490351146002': 45, '4903... 
 {'49035114600': 143, '49035113017': 71, '49035... 
 {'490351146002': 58, '490351146003': 55, '4903... 
 1.046000e-04 
 24656.544455 
 1.715031e-04 
 0.003752 
 0.006851

In [0]:
pdf_sg.groupby('placekey').head()
# type(pdf_sg)

Out[75]:

placekey 
 location_name 
 parent_placekey 
 street_address 
 city 
 date_range_end 
 date_range_start 
 poi_cbg 
 postal_code 
 iso_country_code 
 median_dwell 
 raw_visit_counts 
 raw_visitor_counts 
 visits_by_day 
 region 
 device_type 
 bucketed_dwell_times 
 distance_from_home 
 related_same_day_brand 
 related_same_month_brand 
 visitor_country_of_origin 
 visitor_daytime_cbgs 
 visitor_home_aggregation 
 visitor_home_cbgs 
 normalized_visits_by_total_visits 
 normalized_visits_by_state_scaling 
 normalized_visits_by_total_visitors 
 normalized_visits_by_region_naics_visits 
 normalized_visits_by_region_naics_visitors 
 
 
 
 
 0 
 222-222@5qc-w95-8d9 
 Walmart Neighborhood Market 
 None 
 3555 S 8400 W 
 Magna 
 2021-07-01T00:00:00-06:00 
 2021-06-01T00:00:00-06:00 
 490351139054 
 84044 
 None 
 13.0 
 1686 
 808 
 [47, 46, 57, 61, 62, 56, 48, 80, 48, 39, 60, 5... 
 ut 
 {'android': 533, 'ios': 273} 
 {'<5': 38, '5-10': 661, '11-20': 443, '21-60':... 
 1962.0 
 {'Holiday Oil': 8, '7-Eleven': 7, 'Chevron': 6... 
 {'McDonald's': 55, 'Chevron': 52, 'Holiday Oil... 
 {'US': 795} 
 {'490351139071': 43, '490351139062': 39, '4903... 
 {'49035113905': 117, '49035113907': 117, '4903... 
 {'490351139071': 58, '490351139054': 46, '4903... 
 1.217925e-04 
 28709.208530 
 1.898280e-04 
 0.004369 
 0.007977 
 
 
 1 
 222-222@5ws-h5c-nbk 
 Walmart Supercenter 
 None 
 1550 N Main St 
 North Logan 
 2021-07-01T00:00:00-06:00 
 2021-06-01T00:00:00-06:00 
 490050004011 
 84341 
 None 
 20.0 
 3636 
 1984 
 [124, 130, 137, 156, 159, 80, 119, 118, 103, 9... 
 ut 
 {'android': 1387, 'ios': 590} 
 {'<5': 88, '5-10': 960, '11-20': 903, '21-60':... 
 13726.0 
 {'Build A Bear Workshop': 18, 'Maverik': 9, 'S... 
 {'Maverik': 55, 'McDonald's': 49, 'Build A Bea... 
 {'US': 1930} 
 {'490050004011': 90, '490050005021': 52, '4900... 
 {'49005000202': 138, '49005000403': 100, '4900... 
 {'490050004011': 63, '490050002022': 59, '4900... 
 2.626558e-04 
 61913.809143 
 4.661124e-04 
 0.009422 
 0.017204 
 
 
 2 
 222-223@5qc-zzt-35z 
 Walmart Pharmacy 10 5206 
 None 
 1710 E Skyline Dr 
 South Ogden 
 2021-07-01T00:00:00-06:00 
 2021-06-01T00:00:00-06:00 
 490572112022 
 84405 
 None 
 14.0 
 1 
 1 
 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ... 
 ut 
 {'android': 0, 'ios': 0} 
 {'<5': 0, '5-10': 0, '11-20': 1, '21-60': 0, '... 
 NaN 
 {'Advance Auto Parts': 100, 'Big O Tires': 100} 
 {'Hallmark Cards': 100, 'Walmart': 100, 'Advan... 
 {} 
 {} 
 {} 
 {} 
 7.223756e-08 
 17.028000 
 2.349357e-07 
 0.000005 
 0.000007 
 
 
 3 
 222-226@5qd-2fp-nyv 
 Walmart Pharmacy 10 2921 
 None 
 534 N Harrisville Rd 
 Harrisville 
 2021-08-01T00:00:00-06:00 
 2021-07-01T00:00:00-06:00 
 490572103021 
 84404 
 None 
 19.0 
 1 
 1 
 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ... 
 ut 
 {'android': 0, 'ios': 0} 
 {'<5': 0, '5-10': 0, '11-20': 1, '21-60': 0, '... 
 NaN 
 {'Walgreens': 100} 
 {'Walmart': 100, 'Taco Bell': 100, 'Starbucks'... 
 {'US': 4} 
 {} 
 {} 
 {} 
 7.071859e-08 
 17.417966 
 2.273621e-07 
 0.000004 
 0.000007 
 
 
 4 
 zzw-222@5qc-xty-hnq 
 Walmart Neighborhood Market 
 None 
 1202 W 12600 S 
 Riverton 
 2021-07-01T00:00:00-06:00 
 2021-06-01T00:00:00-06:00 
 490351146003 
 84065 
 None 
 16.0 
 1448 
 730 
 [47, 52, 47, 56, 53, 44, 56, 37, 36, 38, 45, 6... 
 ut 
 {'android': 422, 'ios': 307} 
 {'<5': 39, '5-10': 494, '11-20': 344, '21-60':... 
 3052.0 
 {'Sinclair Oil': 4, 'Vasa Fitness': 3, 'McDona... 
 {'McDonald's': 42, 'Sinclair Oil': 38, 'Maveri... 
 {'US': 694} 
 {'490351146003': 50, '490351146002': 45, '4903... 
 {'49035114600': 143, '49035113017': 71, '49035... 
 {'490351146002': 58, '490351146003': 55, '4903... 
 1.046000e-04 
 24656.544455 
 1.715031e-04 
 0.003752 
 0.006851 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 123 
 zzw-222@5qc-zyv-mkz 
 Walmart Supercenter 
 None 
 2228 W 1700 S

In [0]:
# import altair as alt
# import pandas as pd

In [0]:
%sql
SELECT *
FROM cgjde.test_table
--GROUP BY right(left(date_range_start, 7), 2)

placekey location_name parent_placekey street_address city date_range_end date_range_start poi_cbg postal_code iso_country_code median_dwell raw_visit_counts raw_visitor_counts visits_by_day region device_type bucketed_dwell_times distance_from_home related_same_day_brand related_same_month_brand visitor_country_of_origin visitor_daytime_cbgs visitor_home_aggregation visitor_home_cbgs normalized_visits_by_total_visits normalized_visits_by_state_scaling normalized_visits_by_total_visitors normalized_visits_by_region_naics_visits normalized_visits_by_region_naics_visitors zzw-222@5qc-x2t-cdv Beans & Brews Coffeehouse null 855 W State Rd Ste 103 Pleasant Grove 2021-08-01T00:00:00-06:00 2021-07-01T00:00:00-06:00 490490005091 84062 null 16.0 145 124 List(4, 4, 5, 1, 7, 2, 8, 10, 4, 6, 0, 2, 6, 7, 4, 7, 7, 2, 9, 6, 7, 3, 6, 4, 2, 4, 3, 2, 5, 6, 2) ut Map(android -> 68, ios -> 55) Map(5-10 -> 63, 21-60 -> 38, 61-120 -> 5, <5 -> 3, >240 -> 4, 11-20 -> 20, 121-240 -> 12) 7677 Map(Walmart -> 13, Vasa Fitness -> 7, Target -> 2, Chevron -> 4, Domino's Pizza -> 3, Macey's -> 2, The Home Depot -> 3, Michaels Stores -> 2, 7-Eleven -> 2, Starbucks -> 4, Wendy's -> 4, The Meadows -> 6, Holiday Oil -> 4, Maverik -> 4, Sinclair Oil -> 4, Café Zupas -> 2, Swig -> 2, Curves -> 2, McDonald's -> 2, Mo' Bettahs -> 11) Map(Walmart -> 76, Target -> 30, Chevron -> 52, Taco Bell -> 28, Macey's -> 23, Starbucks -> 33, Wendy's -> 40, The Meadows -> 62, Holiday Oil -> 26, Smith's Food & Drug Stores -> 30, Maverik -> 39, Sinclair Oil -> 29, Costco -> 32, Chick-fil-A -> 38, Walgreens -> 28, McDonald's -> 42, Kneaders Bakery & Cafe -> 25, Phillips 66 -> 26, Mo' Bettahs -> 27, Shell Oil -> 24) Map(US -> 122) Map(490532701001 -> 4, 490490102153 -> 4, 490490102104 -> 4, 490490005091 -> 13, 490211107022 -> 4, 490490005041 -> 4, 490490002052 -> 7, 490490005043 -> 4, 490490005092 -> 4, 060290010003 -> 6, 490490102101 -> 4, 490490102103 -> 4, 490111258051 -> 4, 490490102171 -> 4, 490490004002 -> 4, 490490005062 -> 4, 490351128163 -> 4, 040131167123 -> 4, 490490002032 -> 4, 490490006041 -> 4, 490490005083 -> 4, 490490005072 -> 4, 490490006011 -> 4, 490351128171 -> 4, 490490018031 -> 4, 490490102154 -> 4) Map(49049003402 -> 4, 49049010210 -> 7, 49049000505 -> 4, 49049000509 -> 15, 49049000203 -> 4, 49049010108 -> 4, 49049000901 -> 4, 49049000506 -> 4, 49035112821 -> 4, 04013116712 -> 4, 49049010219 -> 4, 49049002201 -> 4, 49049010215 -> 4, 49049010105 -> 4, 49049000604 -> 4, 49049000205 -> 4, 49007000200 -> 4, 49049000504 -> 6, 49053270100 -> 6, 49049002300 -> 4, 49049000603 -> 4, 49049002102 -> 4, 49049010106 -> 4) Map(490490102191 -> 4, 490532701001 -> 4, 490490007032 -> 4, 490490102104 -> 5, 490490005091 -> 10, 490490005041 -> 4, 490490002052 -> 4, 490490022013 -> 5, 490490104113 -> 4, 490490102103 -> 7, 490490022011 -> 4, 490490101044 -> 4, 490490104061 -> 4, 490490101122 -> 4, 490490005053 -> 4, 490490034022 -> 4, 490490023002 -> 4, 490490002032 -> 4, 490490006041 -> 4, 490490009013 -> 4, 490351128212 -> 4, 490490005083 -> 4, 490490005072 -> 4, 490490006033 -> 4, 490490034021 -> 4, 490490012023 -> 4, 490490006011 -> 4, 490490011051 -> 4, 490490101053 -> 6, 490070002003 -> 4) 1.0254195857828191E-5 2525.6051226806444 2.819289670872941E-5 8.348120060935519E-5 1.1820369512902953E-4 22b-222@5qd-22t-975 Farmers Insurance Group null 1935 W 5200 S Roy 2021-07-01T00:00:00-06:00 2021-06-01T00:00:00-06:00 490572107012 84067 null 44.5 40 22 List(3, 0, 0, 3, 2, 2, 0, 3, 0, 1, 1, 0, 0, 3, 0, 4, 0, 3, 2, 1, 3, 0, 3, 2, 0, 0, 1, 2, 0, 1) ut Map(android -> 19, ios -> 4) Map(5-10 -> 9, 21-60 -> 8, 61-120 -> 3, <5 -> 1, >240 -> 12, 11-20 -> 5, 121-240 -> 2) 3088 Map(Petco -> 6, Sonic -> 3, Walmart -> 18, Chevron -> 6, Cinnabon -> 6, Common Cents -> 3, Taco Bell -> 3, Health Street -> 9, The Salvation Army -> 3, KFC -> 9, T.J. Maxx -> 3, The Home Depot -> 3, Speedway -> 3, 7-Eleven -> 15, Wendy's -> 3, Maverik -> 6, Sinclair Oil -> 15, Harmons -> 6, McDonald's -> 6, Kia Motors -> 6) 

In [0]:
%sql
SELECT raw_visitor_counts, right(left(date_range_start, 7), 2) as month
FROM cgjde.test_table
GROUP BY month, raw_visitor_counts

raw_visitor_counts month 88 07 25 06 111 06 75 07 345 07 126 06 305 06 454 07 95 07 10727 07 447 07 741 07 1738 07 168 07 37 07 134 06 55 06 266 07 136 06 113 07 780 06 310 07 233 06 154 06 591 06 93 07 110 06 121 06 441 06 4213 06 571 07 287 07 457 06 414 06 510 07 559 07 1 06 89 07 141 07 119 06 235 06 528 07 1188 06 213 07 115 07 9 07 795 06 120 06 498 06 741 06 395 07 49 06 8 07 801 07 241 07 84 07 702 07 193 06 163 06 621 06 238 07 102 06 245 06 1067 07 545 06 458 06 575 06 116 06 863 06 440 07 103 06 203 06 460 07 351 07 1233 07 247 07 173 07 123 06 1887 06 515 06 637 07 180 06 509 07 1025 06 1388 07 980 07 191 06 233 07 355 06 359 06 126 07 72 06 2586 06 525 06 182 06 603 07 393 07 238 06 1458 06 513 06 25 07 246 07 890 07 361 07 164 06 128 06 1315 06 578 07 77 06 259 07 795 07 158 07 186 07 187 06 186 06 301 07 599 07 60 07 90 07 668 07 329 06 802 06 20 07 50 07 66 07 513 07 466 06 58 07 367 06 161 07 1715 07 239 06 93 06 91 06 280 07 71 06 592 07 225 06 159 07 428 07 294 06 678 07 254 06 20 06 173 06 800 06 370 06 350 07 23 07 212 06 385 06 931 06 355 07 438 07 317 06 340 06 459 06 95 06 272 06 1081 06 271 06 466 07 504 07 426 07 615 07 32 07 124 06 376 07 307 07 40 06 99 07 342 07 3527 06 761 06 174 06 1579 06 421 06 1249 06 648 07 2217 07 263 06 301 06 43 06 248 07 46 07 1142 07 417 06 541 06 556 06 17 07 1235 07 322 06 216 07 262 07 101 07 3695 07 581 07 611 07 194 07 394 07 74 06 195 07 198 07 357 06 299 07 133 06 70 06 124 07 209 07 332 06 738 07 584 06 319 06 130 07 1760 07 158 06 270 06 224 06 1039 07 348 07 165 07 1127 07 765 07 185 06 177 07 990 06 194 06 408 07 189 06 351 06 170 06 227 06 9 06 161 06 275 06 307 06 588 06 517 06 18 07 145 06 62 06 155 06 168 06 282 07 580 06 479 07 634 07 333 07 12 06 835 06 295 06 2 06 325 07 323 07 798 06 144 07 51 07 188 06 44 06 498 07 1657 06 330 06 1064 06 800 07 4932 07 589 06 405 06 91 07 691 07 2168 07 162 06 337 06 1327 06 228 06 242 06 427 06 92 07 501 07 165 06 487 06 10 06 847 07 1517 06 488 07 306 06 159 06 103 07 12 07 48 07 33 06 1748 07 56 07 28 07 918 07 208 07 131 06 413 06 132 06 130 06 175 07 215 07 65 07 50 06 406 06 410 07 211 06 789 07 999 06 687 07 572 06 53 07 352 06 1431 07 107 07 3 07 236 07 1948 07 465 07 532 07 393 06 727 06 631 06 151 07 42 07 99 06 76 06 276 06 90 06 112 06 401 07 105 07 208 06 443 07 252 07 303 06 223 07 538 06 71 07 567 07 121 07 152 06 341 06 96 07 244 06 151 06 388 07 343 07 202 07 1716 06 214 07 1904 06 667 07 45 06 108 07 1207 07 169 06 661 07 640 06 68 07 70 07 525 07 986 06 133 07 231 07 428 06 122 06 148 06 167 06 637 06 74 07 76 07 172 06 455 06 594 06 456 06 3338 07 564 06 80 07 401 06 340 07 147 06 262 06 10 07 106 07 223 06 982 07 996 06 388 06 253 07 651 06 948 07 386 07 414 07 63 07 803 07 125 06 96 06 192 07 230 06 142 07 289 07 380 07 384 06 879 06 313 07 219 07 477 07 649 07 1926 07 89 06 353 07 363 07 622 06 242 07 23 06 19 06 1100 07 146 07 55 07 160 07 379 07 217 07 222 06 100 06 647 07 86 06 1665 07 59 06 271 07 342 06 635 07 520 06 155 07 136 07 189 07 41 06 514 07 433 07 277 07 3 06 204 06 362 07 728 06 357 07 382 07 2207 06 83 06 154 07 29 06 128 07 36 06 184 07 373 07 255 06 114 07 179 06 429 06 930 06 756 07 492 06 574 06 129 07 387 06 517 07 137 06 934 06 499 07 1533 07 199 06 1024 07 377 07 516 07 259 06 105 06 396 06 232 07 2296 06 318 07 1259 06 2097 07 6838 07 142 06 14 06 328 06 312 06 36 07 222 07 776 06 329 07 270 07 13 06 366 06 67 06 807 07 645 07 444 07 284 07 416 07 1534 06 364 06 31 07 322 07 243 06 119 07 240 07 476 06 508 06 302 07 315 06 864 06 137 07 116 07 156 07 201 07 319 07 220 06 58 06 171 06 122 07 184 06 290 06 56 06 458 07 298 06 135 07 241 06 306 07 421 07 4 06 28 06 79 06 63 06 196 07 584 07 659 07 331 06 110 07 60 06 139 07 140 06 24 07 1335 06 349 07 31 06 497 07 4954 07 216 06 1162 06 213 06 346 06 1802 06 430 06 1153 06 381 07 497 06 113 06 967 07 4 07 361 06 33 07 172 07 665 07 321 06 371 07 1378 07 21 07 43 07 224 07 210 07 281 07 132 07 296 06 183 07 1425 07 291 07 69

In [0]:
%sql

Select raw_visit_counts, right(left(date_range_start, 7), 2) as month
from cgjde.test_table
GROUP BY month, raw_visit_counts

raw_visit_counts month 111 06 88 07 25 06 75 07 356 07 305 06 345 07 126 06 454 07 95 07 459 07 523 07 946 07 447 07 168 07 612 06 1240 06 906 07 625 07 885 06 316 07 37 07 55 06 136 06 134 06 965 07 113 07 233 06 154 06 1290 07 93 07 121 06 110 06 287 07 441 06 457 06 298 07 828 07 414 06 484 07 510 07 559 07 1 06 141 07 89 07 213 07 272 07 119 06 235 06 9 07 963 06 120 06 714 06 498 06 2001 07 928 07 1188 07 115 07 395 07 613 07 163 06 49 06 8 07 84 07 688 06 1494 07 245 06 238 07 324 06 779 07 1624 07 483 07 102 06 575 06 621 06 116 06 440 07 4983 06 920 06 103 06 729 07 351 07 203 06 455 07 491 07 816 06 123 06 637 07 173 07 268 06 1254 07 180 06 191 06 658 06 233 07 858 07 1967 07 72 06 513 06 126 07 40139 06 837 07 182 06 537 07 525 06 1093 06 25 07 361 07 373 06 444 06 890 07 246 07 2667 06 442 07 77 06 578 07 164 06 630 06 282 06 259 07 186 07 187 06 186 06 795 07 158 07 90 07 1550 06 60 07 329 06 968 06 20 07 50 07 66 07 540 06 190 06 461 07 58 07 91 06 161 07 239 06 280 07 93 06 462 06 563 07 5970 07 367 06 397 06 159 07 71 06 294 06 225 06 1222 07 428 07 804 06 528 06 254 06 1023 07 1042 06 20 06 344 07 706 06 173 06 609 06 800 06 370 06 23 07 212 06 512 07 931 06 1083 07 317 06 1754 07 438 07 7228 07 95 06 1601 06 340 06 272 06 1797 06 333 06 466 07 271 06 201 06 504 07 32 07 307 07 124 06 376 07 40 06 174 06 99 07 2452 06 342 07 2863 07 263 06 862 06 894 07 794 06 1419 06 301 06 43 06 46 07 480 07 385 07 593 07 417 06 550 06 2849 07 17 07 819 06 216 07 322 06 262 07 3163 07 535 06 463 07 101 07 919 07 464 07 249 06 667 06 1607 07 469 07 426 06 714 07 581 07 194 07 1178 06 675 06 357 06 195 07 198 07 299 07 74 06 638 06 398 07 124 07 133 06 209 07 332 06 70 06 1941 06 5665 07 742 07 319 06 1314 06 158 06 185 07 130 07 551 07 467 07 394 06 799 06 224 06 165 07 270 06 473 06 300 06 177 07 618 06 185 06 170 06 351 06 1554 07 616 06 189 06 194 06 9 06 161 06 275 06 307 06 62 06 18 07 479 07 333 07 145 06 619 07 168 06 4145 07 155 06 12 06 582 07 872 07 529 07 255 07 478 06 1897 07 1642 06 2 06 5761 06 323 07 4138 06 327 06 144 07 51 07 44 06 188 06 360 06 498 07 242 06 691 07 91 07 427 06 162 06 1719 06 228 06 337 06 92 07 501 07 487 06 165 06 398 06 10 06 565 06 522 07 103 07 736 06 159 06 595 07 33 06 12 07 48 07 202 06 256 07 1375 06 1195 07 2096 07 457 07 1198 07 850 06 56 07 28 07 131 06 629 07 225 07 208 07 1462 07 413 06 215 07 175 07 1041 06 130 06 132 06 211 06 50 06 1286 07 425 07 65 07 940 06 1268 06 1482 07 439 07 406 06 572 06 687 07 53 07 3600 07 3 07 532 06 107 07 393 06 236 07 151 07 90 06 42 07 76 06 276 06 99 06 471 07 112 06 557 07 208 06 655 07 443 07 479 06 105 07 223 07 252 07 296 07 13020 06 855 07 303 06 526 06 96 07 121 07 341 06 152 06 71 07 392 07 567 07 244 06 755 06 202 07 343 07 151 06 388 07 412 06 371 06 1145 07 667 07 214 07 929 06 45 06 666 07 169 06 108 07 7171 07 661 07 640 06 68 07 70 07 1000 06 439 06 133 07 525 07 637 06 167 06 231 07 122 06 148 06 602 06 76 07 74 07 9948 07 172 06 1092 07 456 06 557 06 147 06 419 06 80 07 1747 06 262 06 401 06 953 07 10 07 106 07 633 07 388 06 253 07 223 06 125 06 63 07 1265 07 142 07 230 06 380 07 508 07 432 06 96 06 414 07 803 07 573 06 717 07 1926 07 242 07 89 06 363 07 628 07 19 06 680 07 23 06 146 07 786 07 1054 07 595 06 160 07 55 07 379 07 222 06 3659 07 826 07 86 06 100 06 797 07 59 06 271 07 2886 06 342 06 136 07 189 07 470 06 505 07 939 06 155 07 359 07 41 06 424 07 277 07 433 07 3 06 362 07 2686 06 204 06 861 06 875 06 83 06 154 07 2343 06 634 06 494 07 29 06 36 06 373 07 128 07 255 06 184 07 114 07 492 06 129 07 1163 07 179 06 387 06 429 06 474 07 574 06 756 07 517 07 137 06 934 06 789 06 507 07 772 06 199 06 143 07 232 07 1015 07 259 06 105 06 585 06 1134 07 318 07 406 07 511 07 36 07 14 06 222 07 142 06 329 07 312 06 337 07 328 06 67 06 13 06 257 06 284 07 478 07 1609 06 416 07 322 07 4538 06 31 07 2222 07 243 06 416 06 300 07 1196 06 922 07 119 07 493 07 846 06 315 06 302 07 508 06 1936 06 220 06 116 07 156 07 137 07 201 07 58 06 1

In [0]:
eTable2iiiString = spark.sql(
  """
  select location_name, array_join(visits_by_day, ',') as myCol, right(left(date_range_start, 7), 1) as month
  from cgjde.test_table
  order by location_name desc
  """
)


eTable2iiiString2 = spark.sql(
  """
  select location_name, array_join(visits_by_day, ',') as myCol
  from cgjde.test_table
  order by location_name asc
  """
)


from pyspark.sql.functions import split, explode
eTable2iiiString.withColumn('myCol',explode(split('myCol',','))).show()


+--------------------+-----+-----+
 location_name|myCol|month|
+--------------------+-----+-----+
zhang's Chinese k...| 6| 6|
zhang's Chinese k...| 9| 6|
zhang's Chinese k...| 13| 6|
zhang's Chinese k...| 14| 6|
zhang's Chinese k...| 5| 6|
zhang's Chinese k...| 0| 6|
zhang's Chinese k...| 6| 6|
zhang's Chinese k...| 10| 6|
zhang's Chinese k...| 4| 6|
zhang's Chinese k...| 5| 6|
zhang's Chinese k...| 7| 6|
zhang's Chinese k...| 6| 6|
zhang's Chinese k...| 1| 6|
zhang's Chinese k...| 2| 6|
zhang's Chinese k...| 4| 6|
zhang's Chinese k...| 4| 6|
zhang's Chinese k...| 7| 6|
zhang's Chinese k...| 8| 6|
zhang's Chinese k...| 8| 6|
zhang's Chinese k...| 1| 6|
+--------------------+-----+-----+
only showing top 20 rows

In [0]:
eTemp = dfsg.filter(dfsg['date_range_start'].like('%2021-06-01%'))
eTemp = eTemp.select("date_range_start", "visits_by_day")
eTemp = eTemp.rdd.map(lambda x:[int(y) for y in x['visits_by_day']]).toDF(['1','2','3','4','5','6','7','8','9','10','11','12','13','14','15','16','17','18','19','20','21','22','23','24','25','26','27','28','29','30'])
display(eTemp)

1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 2 3 0 1 0 1 2 0 0 0 1 0 1 0 1 0 2 2 1 0 1 3 1 0 1 0 7 0 1 0 1 4 0 2 4 3 0 3 3 1 5 3 1 1 6 1 0 1 5 4 1 3 1 0 2 1 2 0 2 0 1 1 0 0 1 0 2 1 5 0 0 0 0 1 0 0 1 0 0 2 3 3 4 0 1 3 0 4 5 3 12 16 10 2 1 1 10 5 3 4 13 7 0 3 3 2 1 3 0 0 0 2 0 1 1 0 0 3 3 1 0 2 3 3 5 3 3 3 2 3 3 5 6 2 5 2 1 3 3 2 4 2 3 3 1 4 3 2 1 1 0 0 1 4 3 0 3 1 0 0 2 3 5 3 0 1 2 0 3 2 6 2 3 2 4 1 1 3 1 2 2 4 4 2 4 0 4 2 1 2 2 1 1 2 4 1 1 1 1 0 1 0 0 0 0 2 0 1 1 2 16 20 14 7 36 0 13 19 8 12 13 1 3 17 19 9 13 3 2 0 10 16 8 11 7 1 3 21 17 11 0 1 6 3 8 6 4 5 4 3 9 13 8 3 2 1 2 10 14 2 0 1 0 3 8 5 2 7 0 1 139 155 161 168 194 129 149 131 139 127 126 175 136 166 149 155 163 175 236 112 164 140 143 145 166 208 102 188 153 141 3 4 1 3 11 0 5 5 2 6 2 9 0 3 1 1 4 2 6 0 2 5 4 1 3 4 0 3 3 0 1 2 0 0 0 0 1 0 0 0 0 0 0 1 1 0 1 0 0 0 1 0 1 0 1 0 1 1 0 0 3 1 4 3 5 1 0 5 4 7 1 7 6 3 3 3 4 5 4 4 8 3 7 3 5 2 3 1 3 5 6 8 5 5 2 6 9 5 6 6 4 2 7 9 9 14 6 5 0 5 16 10 11 5 5 3 4 9 11 7 1 0 0 0 2 0 4 4 0 0 1 1 0 1 2 4 1 1 2 0 1 2 1 0 2 3 0 0 0 0 15 14 14 9 3 6 20 10 11 20 11 3 5 19 19 18 12 14 6 8 13 18 22 22 18 5 1 29 11 14 13 8 16 11 9 0 8 11 8 9 10 8 2 7 12 9 9 11 9 2 12 13 13 10 8 7 0 10 15 11 6 7 19 44 27 14 5 6 29 19 22 18 7 34 22 12 19 34 35 20 15 20 32 48 51 50 18 22 16 28 5 4 1 0 0 3 2 4 4 3 0 1 1 6 4 12 8 1 0 1 5 10 11 8 4 3 3 12 12 6 1 2 1 0 0 1 2 0 5 1 1 0 0 3 4 4 3 0 1 0 0 1 1 1 1 0 0 1 0 0 2 2 1 1 4 2 2 1 1 3 2 4 0 3 2 1 2 1 2 0 1 2 3 3 0 1 2 4 2 3 0 3 3 3 5 0 5 2 6 6 4 2 0 1 8 2 6 8 1 3 2 1 3 1 1 1 0 1 3 5 11 8 6 3 2 3 9 9 7 6 3 0 2 10 9 9 8 3 3 4 9 11 13 11 1 2 7 9 8 5 8 9 11 8 5 6 11 7 9 12 7 0 1 9 6 4 5 8 2 4 5 8 9 10 11 3 2 11 12 8 3 3 0 2 2 7 4 5 3 1 4 3 3 0 5 2 3 9 15 17 2 4 1 4 2 1 1 2 5 4 1 9 2 3 9 2 2 0 6 3 0 6 2 4 9 18 10 0 2 0 3 7 18 8 0 6 2 2 7 4 5 5 7 8 5 5 3 3 4 3 5 4 4 4 7 7 6 11 3 2 3 3 4 4 3 2 6 5 6 8 6 3 2 3 0 0 6 5 4 4 1 1 0 8 1 2 0 2 0 0 7 6 7 2 2 0 0 7 3 6 0 0 0 0 0 4 0 0 0 0 0 2 0 0 0 1 2 1 0 1 0 0 0 2 0 0 1 0 0 0 50 25 19 39 64 33 33 43 19 28 32 24 18 21 26 14 22 17 57 10 7 23 16 34 46 37 21 11 44 11 6 7 3 5 8 3 5 4 4 6 6 8 3 3 7 4 4 8 5 0 5 5 2 4 5 9 4 9 5 5 25 23 29 15 25 18 16 18 13 9 23 17 9 19 15 15 15 21 24 18 17 13 17 15 19 16 7 13 24 10 3 13 8 15 9 0 12 4 5 7 5 13 1 4 5 4 9 8 15 1 5 1 3 1 5 8 0 10 10 6 2 4 3 5 1 0 4 4 2 5 3 0 0 3 2 4 2 3 2 0 2 5 3 5 1 1 0 3 7 2 0 2 2 2 0 1 1 1 0 1 1 1 0 1 2 1 3 6 0 1 0 5 1 2 0 0 0 0 2 0 1 2 1 1 3 0 0 1 1 0 1 4 3 1 3 1 1 2 1 1 2 0 1 2 2 2 1 3 0 2 1 0 1 0 1 0 0 0 1 0 0 3 1 1 1 0 0 0 2 0 0 0 2 1 0 0 1 2 0 0 5 8 6 4 6 15 6 7 6 5 10 9 11 6 6 6 9 5 10 3 12 3 10 2 8 3 3 7 8 1 1 2 0 0 2 1 1 0 1 1 3 0 0 0 0 0 1 0 1 1 1 0 0 0 1 16 0 1 1 0 10 9 2 5 16 2 7 5 6 5 6 7 4 4 6 7 7 4 14 5 7 3 3 12 4 7 4 6 5 10 7 10 6 13 11 13 5 3 9 6 5 12 9 8 6 5 8 7 6 21 6 7 6 6 10 10 11 3 8 2 35 25 25 24 28 2 17 18 15 18 33 29 3 23 19 12 19 28 25 0 13 13 18 30 28 30 0 21 12 17 11 13 11 18 20 0 11 7 10 18 14 9 0 10 12 14 10 19 32 0 6 18 13 13 14 16 0 12 9 11 9 12 10 14 2 0 12 12 9 8 7 2 0 11 9 13 9 13 1 0 19 12 19 18 9 1 0 13 14 14 6 7 6 5 0 0 7 8 6 7 7 8 4 3 4 5 8 7 9 4 9 12 6 9 9 10 5 4 8 15 4 0 1 2 1 1 1 2 1 0 2 2 0 2 2 0 0 1 3 2 1 2 4 2 0 0 2 1 1 2 0 0 1 0 0 0 1 0 0 1 0 0 0 0 0 1 0 0 0 0 0 0 0 0 1 1 0 0 0 0 4 3 1 1 1 0 2 1 1 1 2 1 0 2 4 1 0 1 0 0 1 0 1 2 0 0 0 2 1 2 4 2 5 5 0 0 4 5 3 8 4 0 0 8 5 9 5 7 0 0 8 4 8 6 5 1 0 4 3 3 6 4 5 7 0 0 8 8 9 7 4 0 0 7 5 7 5 5 0 0 4 4 4 7 6 0 0 10 7 3 0 1 2 0 1 1 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 0 0 0 1 1 15 10 12 7 12 0 8 2 6 13 25 20 0 7 1 8 7 7 7 0 10 4 5 6 6 1 1 3 1 0 1 2 4 3 6 7 2 3 2 3 4 6 2 3 2 5 0 4 2 0 1 4 2 1 1 3 2 3 4 1 6 13 12 10 2 1 8 11 8 11 11 3 1 9 11 11 8 6 2 3 13 8 14 7 10 3 1 7 10 16 6 6 7 8 8 1 9 5 12 6 8 5 4 10 8 6 7 4 6 2 8 20 4 15 3 6 1 10 8 4 2 0 3 3 1 2 6 3 2 0 1 0 1 0 1 1 0 0 1 0 0 0 3 2 0 2 0 1 1 1 2 0 0 0 2 1 1 1 0 0 0 1 1 0 0 1 1 0 2 4 2 1 1 1 2 1 0 2 3 2 19 11 14 10 12 4 14 14 14 9 12 8 3 8 13 18 16 9 11 7 14 10 7 10 9 4 0 7 7 6 0 1 1 1 1 1 1 4 4 0 2 0 3 1 0 0 0 2 0 2 2 0 1 0 2 0 1 1 0 0 2 2 2 0 0 1 

In [0]:
triple_i = target_df.toPandas()

In [0]:
%sql

Select 
  right(left(date_range_start, 7), 1) as month
from cgjde.test_table

month 7 6 6 7 6 6 7 7 7 7 7 6 6 7 6 6 7 7 6 7 7 6 7 7 6 7 6 7 7 7 7 7 6 7 6 7 7 7 6 6 7 7 6 7 7 7 6 7 7 6 7 6 6 7 6 7 6 6 7 6 7 6 6 6 7 6 7 6 7 7 6 7 7 7 6 7 7 6 6 6 6 7 7 7 7 6 6 7 6 6 7 7 7 6 7 7 7 6 6 7 6 6 6 6 7 6 7 6 7 6 6 6 6 6 6 7 7 6 7 7 7 7 7 6 6 6 7 7 7 7 6 6 7 7 6 7 6 7 6 6 6 6 6 7 6 6 7 6 7 7 6 7 6 6 6 6 6 7 7 7 6 7 7 6 7 7 6 6 6 7 6 7 6 6 6 7 6 6 6 6 6 6 6 6 6 6 7 7 6 6 6 6 7 7 6 6 6 7 7 7 6 7 6 6 7 7 7 6 7 7 6 7 6 6 7 7 7 6 7 7 6 6 6 6 7 7 7 7 7 7 6 7 6 7 7 6 7 6 6 6 7 7 7 6 6 6 7 7 7 7 6 6 6 6 7 7 7 7 7 7 6 6 7 6 6 7 7 6 7 6 7 6 7 7 6 6 6 7 6 6 7 7 6 7 6 7 6 6 7 6 6 7 7 6 6 7 6 7 6 6 7 6 7 7 6 7 7 7 7 7 7 7 7 7 7 7 7 7 7 6 7 6 6 7 7 6 7 6 7 7 7 6 7 7 6 7 6 6 6 7 7 7 6 7 7 7 7 7 7 7 6 7 7 7 6 6 7 7 6 6 6 6 6 6 7 6 6 6 7 7 6 7 6 7 7 6 6 7 7 7 7 7 6 6 6 7 6 7 6 6 6 7 7 7 7 6 6 7 6 6 7 7 6 6 7 6 7 6 6 6 6 7 7 7 7 6 7 6 7 7 7 7 7 6 7 7 7 7 7 7 6 6 7 7 7 7 6 7 7 6 6 6 6 6 7 6 7 6 7 6 7 6 6 6 7 6 6 7 6 6 7 6 6 7 7 7 6 6 7 6 7 7 7 6 6 6 6 7 7 6 6 7 7 7 6 6 7 6 6 6 6 7 7 7 6 6 7 6 7 7 6 7 7 6 6 6 6 6 6 6 6 6 6 7 6 7 6 6 7 7 7 6 7 6 6 6 7 6 7 7 7 7 6 6 7 6 7 6 6 7 7 7 7 7 6 7 7 6 6 7 6 6 7 6 7 6 6 7 6 7 6 7 7 6 7 7 6 7 7 6 7 6 7 6 6 6 6 7 6 7 6 6 6 6 6 7 7 7 6 7 7 7 6 7 7 6 6 7 7 6 7 6 6 7 7 7 6 6 6 6 6 6 6 6 6 6 6 6 6 6 6 7 6 7 7 7 7 6 7 7 7 7 6 6 6 7 6 6 6 7 6 7 6 6 6 6 6 7 7 6 6 7 6 7 7 7 6 7 6 7 6 7 7 6 6 7 7 7 7 7 6 7 6 7 7 7 6 7 7 7 7 6 6 7 6 7 6 6 6 6 6 7 6 7 6 6 7 6 6 7 6 7 7 7 7 6 6 7 7 7 7 6 7 7 6 6 6 7 6 7 6 6 6 7 7 6 6 7 6 6 6 6 7 7 7 6 7 7 6 7 6 7 6 6 7 6 6 7 6 6 6 7 6 6 6 7 7 6 6 6 7 7 7 6 6 6 7 6 7 6 7 7 7 6 6 6 6 6 6 7 7 6 7 6 6 7 7 6 6 6 7 6 7 7 7 6 7 7 7 7 6 7 7 7 7 7 6 6 7 6 7 7 6 6 7 6 7 7 6 7 6 7 6 6 7 6 7 6 7 6 6 6 7 7 7 7 7 6 6 7 6 6 6 6 7 7 7 6 6 7 6 6 7 6 7 6 7 7 6 7 6 6 6 6 7 7 6 6 7 6 7 6 7 7 6 7 6 6 7 7 6 6 7 7 6 7 7 7 7 6 7 7 6 7 6 7 7 6 6 6 7 6 7 6 7 6 6 7 7 6 6 7 6 7 6 6 6 7 7 6 6 7 6 7 6 6 7 6 7 6 7 7 7 6 6 6 6 7 7 6 7 7 6 6 6 6 6 7 6 6 7 6 6 7 7 7 6 7 6 7 6 7 7 7 6 7 6 6 6 7 6 7 7 6 7 6 6 7 6 7 6 7 6 7 7 7 7 7 7 7 7 6 7 7 6 7 7 6 7 7 Showing the first 1000 rows.

# PART 3
Use the data from the created table to create two summary tables (Team)

In [0]:
p3i = spark.sql(#"Select DISTINCT ")
  """
  SELECT left(date_range_start, 10) as Start_Date, count(DISTINCT placekey)
  FROM cgjde.test_table 
--   WHERE location_name = "Starbucks"
  group by Start_Date
  
  """
)

p3i.columns

p3iPandas = p3i.toPandas()
p3iPandas

Out[80]:

Start_Date 
 count(DISTINCT placekey) 
 
 
 
 
 0 
 2021-07-01 
 30200 
 
 
 1 
 2021-06-01 
 30005

In [0]:
# %sql
p3ii = spark.sql(
"""
  SELECT DISTINCT city, COUNT(placekey) as num_unique_records
  FROM cgjde.test_table
  GROUP BY city
  ORDER BY num_unique_records DESC
  LIMIT 10
""")

p3iiPandas = p3ii.toPandas()
p3iiPandas

Out[81]:

city 
 num_unique_records 
 
 
 
 
 0 
 Salt Lake City 
 7217 
 
 
 1 
 Orem 
 2149 
 
 
 2 
 Sandy 
 2130 
 
 
 3 
 Ogden 
 2074 
 
 
 4 
 Provo 
 1813 
 
 
 5 
 West Valley City 
 1766 
 
 
 6 
 Murray 
 1665 
 
 
 7 
 St George 
 1612 
 
 
 8 
 West Jordan 
 1544 
 
 
 9 
 Layton 
 1299